# Verkehrsszenario_Verhaltensprädiktion

Es soll vorausgesagt werden, ob ein Fahrzeug in einer gegebenen Verkehrssituation das vorausfahrende Fahrzeug überholen wird. Dazu werden der Abstand und die Geschwindigkeit zum vorausfahrenden Fahrzeug gemessen. Zudem wird diese Information von einem Fahrzeug auf der linken Spur gemessen, welches sich von hinten nähert. Als weitere Informationen liegen die jeweiligen Fahrzeugtypen, das Wetter, die Tageszeit und die Straßenart und -krümmung vor.

Mögliche vorherzusagende Reaktionen des Fahrzeugs sind: Geschwindigkeit und Spur beibehalten (continue), Verzögern (decelerate), Spurwechsel bei gleicher Geschwindigkeit (lane change) und Spurwechsel mit Beschleunigung (accelerated lane change).
Entwerfen Sie dazu ein geeignetes Ähnlichkeitsmaß und ermitteln Sie eine Repräsentation des Modells mit Hilfe von Case Based Learning (Verfahren aus der Vorlesung)

## Aufgabenstellung
Entwickeln Sie eine Software, welche bei Eingabe einer Verkehrssituation (im gleichen Format) die Aktion des Fahrzeugs voraussagen kann. Diskutieren Sie Ihre Konfiguration und das Ergebnis.

## Eingangsdaten
Ein Datensatz von Messungen in welchem ähnliche Situationen aufgezeichnet wurden -> data/SIM_001.csv

In [ ]:
# Imports
from model import *
from similarity import *
import csv

In [ ]:
def create_similarity_matrix(filename, key):
    """ 
    Generates similarity matrix 
    
    Arguments:
        filename: the csv file name as string
        key: the title of the csv which is the value in the first line and col

    Returns:
        similarity dict
    """
    with open(filename) as file:
        similarity_matrix = {}

        for line in csv.DictReader(file, skipinitialspace=True):
            for k, v in line.items():
                if k == key:
                    key_v = v
                    similarity_matrix[key_v] = {}
                else:
                    similarity_matrix[key_v][k] = float(v)

        return similarity_matrix

In [ ]:
"""
Read data/SIM_001.csv
"""
case_base_obj = CaseBase.from_csv(
    "data/SIM_001.csv",
    problem_fields = ("v", "v_left", "v_front", "d_left", "d_front", "type_left", "type_front", "radius_curve(m)", "slope_street", "street_type", "time", "weather", "type_vehicle", "speed_limit(km/h)"),
    solution_fields = ("action"),
    encoding = "utf-8",
    delimiter = ";",
    set_int = True
)

In [ ]:
"""
Read similarity matrices.
    data/vehicle_type_sim.csv
    data/street_slope_sim.csv
    data/street_type_sim.csv
    data/time_type_sim.csv
    data/weather_type_sim.csv
"""
case_base_obj.add_symbolic_sim(
    field = "type_left",
    similarity_matrix = create_similarity_matrix("data/vehicle_type_sim.csv", "type_vehicle")
)

case_base_obj.add_symbolic_sim(
    field = "type_front",
    similarity_matrix = create_similarity_matrix("data/vehicle_type_sim.csv", "type_vehicle")
)

case_base_obj.add_symbolic_sim(
    field = "type_vehicle",
    similarity_matrix = create_similarity_matrix("data/vehicle_type_sim.csv", "type_vehicle")
)

case_base_obj.add_symbolic_sim(
    field = "slope_street",
    similarity_matrix = create_similarity_matrix("data/street_slope_sim.csv", "type_street_slope")
)

case_base_obj.add_symbolic_sim(
    field = "street_type",
    similarity_matrix = create_similarity_matrix("data/street_type_sim.csv", "type_street")
)

case_base_obj.add_symbolic_sim(
    field = "time",
    similarity_matrix = create_similarity_matrix("data/time_type_sim.csv", "type_time")
)

case_base_obj.add_symbolic_sim(
    field = "weather",
    similarity_matrix = create_similarity_matrix("data/weather_type_sim.csv", "type_weather")
)

In [ ]:
# TODO Read query from cli
query = Query.from_problems(
    v = 28.5,
    v_left = 42.5,
    v_front = 5,
    d_left = -137,
    d_front = 54,
    type_left = "motorcycle",
    type_front = "truck",
    radius_curve = 2391,
    slope_street = "flat",
    street_type = "country_road (separated)",
    time = "day",
    weather = "dry",
    type_vehicle = "car",
    speed_limit = 100,
)

# sim_funcs: manhattan_sim, euclid_sim
retrieved = case_base_obj.retrieve(
    query,
    v_left = euclid_sim,
    v_front = euclid_sim,
    d_left = euclid_sim,
    d_front = euclid_sim,
    type_left = symbolic_sim,
    type_front = symbolic_sim,
    radius_curve = euclid_sim,
    slope_street = symbolic_sim,
    street_type = symbolic_sim,
    time = symbolic_sim,
    weather = symbolic_sim,
    type_vehicle = symbolic_sim,
    speed_limit = euclid_sim,
)

print("Your Query:")
for k, v in query.problem.items():
    print(f"  - {k} = {v}")
print()
print("Prediction: " + " ".join(retrieved.solution.values()).capitalize())
print()
print("Explanation:")
for field, val in retrieved.sim_per_field.items():
    print(f"  - {field} =", retrieved.problem[field], f"(similarity: {val:.2f})")